Published on July 01, 2023. By Marília Prata, mpwolke.

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/aslfr-preprocessing-dataset.zip
/kaggle/input/icr-identify-age-related-conditions.zip
/kaggle/input/learning-equality-curriculum-recommendations.zip
/kaggle/input/cafa-5-protein-function-prediction.zip
/kaggle/input/hubmap-hacking-the-human-vasculature.zip
/kaggle/input/learning-equality-curriculum-recommendations/correlations.csv
/kaggle/input/learning-equality-curriculum-recommendations/sample_submission.csv
/kaggle/input/learning-equality-curriculum-recommendations/content.csv
/kaggle/input/learning-equality-curriculum-recommendations/topics.csv
/kaggle/input/aslfr-preprocessing-dataset/STDS.npy
/kaggle/input/aslfr-preprocessing-dataset/MEANS.npy
/kaggle/input/aslfr-preprocessing-dataset/X_val.npy
/kaggle/input/aslfr-preprocessing-dataset/y_val.npy
/kaggle/input/aslfr-preprocessing-dataset/y.npy
/kaggle/input/aslfr-preprocessing-dataset/X.npy
/kaggle/input/aslfr-preprocessing-dataset/y_train.npy
/kaggle/input/aslfr-preprocessing-dataset/X_train.npy
/kaggle/input/aslfr-

#I didn't know that we could draw with Python. Let's check those amazing kagglers performances.

In [2]:
! pip install mediapipe -qq

#Victor nailed on Google American Sign Language Competition. Check Victor's Dumetz work.

And maybe you could join that Competition too, there is still two months to go.

In [3]:
#By Victor Dumetz https://www.kaggle.com/code/victordumetz/gaslfr-svg-visualisation

import json
import os

from IPython.display import HTML
from mediapipe import solutions as mp
import numpy as np
import pandas as pd


INPUT_DIR = "/kaggle/input/asl-fingerspelling"
OUTPUT_DIR = "/kaggle/working"

HAND_CONNECTIONS = mp.hands_connections.HAND_CONNECTIONS
POSE_CONNECTIONS = mp.pose_connections.POSE_CONNECTIONS
FACE_CONNECTIONS = mp.face_mesh_connections.FACEMESH_CONTOURS

In [4]:
#By Victor Dumetz https://www.kaggle.com/code/victordumetz/gaslfr-svg-visualisation

df = pd.read_csv(os.path.join(INPUT_DIR, "train.csv"))
sup_df = pd.read_csv(os.path.join(INPUT_DIR, "supplemental_metadata.csv"))

In [5]:
#By Victor Dumetz https://www.kaggle.com/code/victordumetz/gaslfr-svg-visualisation

def get_full_landmark_path(path):
    return os.path.join(INPUT_DIR, path)

landmarks = pd.read_parquet(get_full_landmark_path(df.loc[0]["path"]))

selected_columns = list(landmarks.columns[~landmarks.columns.str.startswith('z_')])
inference_args = {"selected_columns": selected_columns}

with open(os.path.join(OUTPUT_DIR, "inference_args.json"), "w") as f:
    json.dump(inference_args, f)

with open(os.path.join(OUTPUT_DIR, "inference_args.json")) as f:
    inference_args = json.load(f)
    SELECTED_COLUMNS = inference_args["selected_columns"]

def get_nan_ranges(sequence):
    """Get list of frame indices that start or end a nan sequence.

    The first index corresponds to the frame of the first missing value. The following
    indices correspond to every bound of missing or valid value range.

    Args:
        sequence (pd.DataFrame): The sequence landmarks data.

    Returns:
        dict: Dictionary with landmarks as index and lists of frame indices as values.
    """
    # keep only x since missing x => missing y
    s = sequence["x"]

    # replace keypoints with landmarks since a missing keypoint => missing landmark
    s = s.reset_index("keypoint")
    s["keypoint"] = s["keypoint"].str.replace(r"_[0-9]+", "", regex=True)
    s.rename({"keypoint": "landmark"}, axis=1, inplace=True)
    s = s.reset_index().set_index(["landmark", "frame"])
    s = s.groupby(["landmark", "frame"]).mean()["x"]

    # for each landmark and range of missing value returns a df with landmark as key
    # and start and end frame of the range as values
    m = s.isnull()
    nan_ranges = [
        g.reset_index("frame").groupby("landmark").agg(start=("frame", "min"), end=("frame", "max"))
        for _, g in s[m].groupby((~m).groupby(level="landmark").cumsum())
    ]

    # extract start and end and flatten
    nan_ranges = {
        r.index[0]: [
            rrr for rr in nan_ranges for rrr in (rr.start.squeeze(), rr.end.squeeze()) if rr.index[0] == r.index[0]
        ]
        for r in nan_ranges
    }

    return nan_ranges


def animate_hidden_attribute(landmark_nan_ranges, n_frames, dur):
    """Generate an <animate /> tag that hides the landmark when its coordinates are nan.

    Args:
        landmark_nan_ranges (list): List of frame indices that start or end a nan sequence.
        n_frames (int): Length of the sequence.
        dur (float): Frame duration (in seconds).

    Returns:
        str: <animate /> tag for the hidden attribute.
    """
    landmark_nan_ranges = list(landmark_nan_ranges / n_frames)

    v = (";").join(["visible"] + ["hidden", "visible"] * (len(landmark_nan_ranges) // 2) + ["visible"])
    kt = (";").join([str(k) for k in [0.0] + landmark_nan_ranges + [1.0]])

    return f'<animate attributeName="visibility" values="{v}" dur="{dur}s" keyTimes="{kt}" repeatCount="indefinite"/>'


def animate_attribute(attribute_name, values, dur):
    """Generate an <animate /> tag for the given attribute.

    Args:
        attribute_name (str): Name of the attribute to animate.
        values (str): Values to be taken by the attribute, separated by semicolons.
        dur (float): Frame duration (in seconds).

    Returns:
        str: <animate /> tag for the given attribute.
    """
    return f'<animate attributeName="{attribute_name}" values="{values}" dur="{dur}" repeatCount="indefinite"/>'


def draw_connection(x0, x1, y0, y1, landmark_nan_ranges, n_frames, fps, color="black", stroke_width=0.001):
    """Generate a <line></line> block for a connection its animation.

    Args:
        x0 (float): x0 coordinate.
        x1 (float): x1 coordinate.
        y0 (float): y0 coordinate.
        y1 (float): y1 coordinate.
        landmark_nan_ranges (list): List of frame indices that start or end a nan sequence.
        n_frames (int): Number of frames in the sequence.
        fps (int): FPS used for the animation.
        color (str, optional): Color of the connection. Defaults to "black".
        stroke_width (float, optional): Width of the stroke. Defaults to 0.001.

    Returns:
        str: <line></line> block for the connection.
    """
    dur = n_frames / fps
    animation = "".join(
        [
            animate_attribute("x1", ";".join(x0.values), dur),
            animate_attribute("x2", ";".join(x1.values), dur),
            animate_attribute("y1", ";".join(y0.values), dur),
            animate_attribute("y2", ";".join(y1.values), dur),
        ]
    )
    set_hidden = animate_hidden_attribute(landmark_nan_ranges, n_frames, dur)

    return f'<line stroke="{color}" stroke-width="{stroke_width}">{animation}{set_hidden}</line>'

In [6]:
#By Victor Dumetz https://www.kaggle.com/code/victordumetz/gaslfr-svg-visualisation

def load_landmarks(path, selected_colums=SELECTED_COLUMNS):
    return pd.read_parquet(get_full_landmark_path(path), columns=selected_colums)

def load_sequence(sequence_id, data, selected_columns=SELECTED_COLUMNS):
    path = data.loc[data["sequence_id"] == sequence_id, "path"].squeeze()
    landmarks = load_landmarks(path, selected_columns)
    return landmarks.loc[sequence_id]

def visualise_sequence(sequence_id, data, selected_columns=None, fps=10):
    """Generate an animated SVG file for visualising the sequence.

    Args:
        sequence_id (int): Sequence ID.
        data (pd.DataFrame): Metadata from where to find the path to the landmarks file.
        data_dir (str): Path to the data directory.
        selected_columns (list, optional): Subset of columns to be loaded. Defaults to None.
        fps (int, optional): FPS used for the animation. Defaults to 10.

    Returns:
        HTML: SVG animation of the sequence.
    """
    if selected_columns is not None and "frame" not in selected_columns:
        selected_columns.append("frame")

    phrase = data.loc[data["sequence_id"] == sequence_id, "phrase"].squeeze()
    sequence = load_sequence(sequence_id, data, selected_columns)
    sequence = sequence.loc[:, ~sequence.columns.str.startswith("z_")]

    sequence.sort_values("frame")

    n_frames = sequence["frame"].max()

    sequence_m = sequence.melt("frame").rename({"variable": "keypoint"}, axis=1)
    sequence_m.set_index("keypoint", inplace=True)
    sequence_m.index = sequence_m.index.str.split(pat="_", n=1, expand=True)
    sequence_m.reset_index(inplace=True)
    sequence_m.rename({"level_0": "axis", "level_1": "keypoint"}, axis=1, inplace=True)
    mux = pd.MultiIndex.from_product([sequence_m["keypoint"].unique(), range(n_frames)], names=["keypoint", "frame"])
    sequence_m = sequence_m.pivot(index=["frame", "keypoint"], columns="axis").reorder_levels(["keypoint", "frame"])
    sequence_m = sequence_m.reindex(mux)
    sequence_m.sort_index(level=["keypoint", "frame"], ascending=[1, 1], inplace=True)
    sequence_m.columns = ["x", "y"]

    min_x = np.nanmin(sequence_m["x"])
    max_x = np.nanmax(sequence_m["x"])
    min_y = np.nanmin(sequence_m["y"])
    max_y = np.nanmax(sequence_m["y"])
    pad = 0.1

    nan_ranges = get_nan_ranges(sequence_m)

    sequence_str = sequence_m.groupby(level="keypoint").ffill().astype(str)

    lines = ""
    for _, (i, j) in enumerate(POSE_CONNECTIONS):
        try:
            lines = lines + draw_connection(
                sequence_str.loc[("pose_{}".format(i), slice(None)), "x"],
                sequence_str.loc[("pose_{}".format(j), slice(None)), "x"],
                sequence_str.loc[("pose_{}".format(i), slice(None)), "y"],
                sequence_str.loc[("pose_{}".format(j), slice(None)), "y"],
                nan_ranges.get("pose", []),
                n_frames,
                fps,
                color="black",
            )
        except KeyError:
            pass
    for _, (i, j) in enumerate(FACE_CONNECTIONS):
        try:
            lines = lines + draw_connection(
                sequence_str.loc[("face_{}".format(i), slice(None)), "x"],
                sequence_str.loc[("face_{}".format(j), slice(None)), "x"],
                sequence_str.loc[("face_{}".format(i), slice(None)), "y"],
                sequence_str.loc[("face_{}".format(j), slice(None)), "y"],
                nan_ranges.get("face", []),
                n_frames,
                fps,
                color="black",
            )
        except KeyError:
            pass
    for _, (i, j) in enumerate(HAND_CONNECTIONS):
        try:
            lines = (
                lines
                + draw_connection(
                    sequence_str.loc[("right_hand_{}".format(i), slice(None)), "x"],
                    sequence_str.loc[("right_hand_{}".format(j), slice(None)), "x"],
                    sequence_str.loc[("right_hand_{}".format(i), slice(None)), "y"],
                    sequence_str.loc[("right_hand_{}".format(j), slice(None)), "y"],
                    nan_ranges.get("right_hand", []),
                    n_frames,
                    fps,
                    color="red",
                    stroke_width=0.01,
                )
                + draw_connection(
                    sequence_str.loc[("left_hand_{}".format(i), slice(None)), "x"],
                    sequence_str.loc[("left_hand_{}".format(j), slice(None)), "x"],
                    sequence_str.loc[("left_hand_{}".format(i), slice(None)), "y"],
                    sequence_str.loc[("left_hand_{}".format(j), slice(None)), "y"],
                    nan_ranges.get("left_hand", []),
                    n_frames,
                    fps,
                    color="red",
                    stroke_width=0.01,
                )
            )
        except KeyError:
            pass

    html = f'<h2>{sequence_id} - "{phrase}"</h2>'
    html += '<svg height="600" width="{}" viewBox="{} {} {} {}">{}</svg>'.format(
        600 * (max_x - min_x + 2 * pad) / (max_y - min_y + 2 * pad),
        min_x - pad,
        min_y - pad,
        max_x + pad,
        max_y + pad,
        lines,
    )

    return HTML(html.format(lines))

In [7]:
#By Victor Dumetz https://www.kaggle.com/code/victordumetz/gaslfr-svg-visualisation

for i, row in df.head(3).iterrows():
    display(visualise_sequence(row.sequence_id, df))

#I can only do that

![](https://media.tenor.com/9C-SsTkyc8cAAAAM/middle-finger-homer-simpson.gif)tenor

#We can't forget Santas Competitions 

On my first Santas (2019), due to the Competition title, I thought it was for beginners.

When I saw the "Big Guys" joining with their codes and topics. I found out that Santas isn't for amateurs. However, I had already published my "Competitions are Rock'n'Roll Notebook as a gift for them.

#Take a look on Griffh's beautiful work on Santas 2022 

In [8]:
#By Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
import matplotlib.collections as mc
import numpy as np
import pandas as pd
from functools import *
from itertools import *
from pathlib import Path
from PIL import Image
import tqdm
from sklearn.cluster import KMeans
from scipy.sparse import dok_matrix
from scipy.sparse.csgraph import minimum_spanning_tree
import copy
import warnings
warnings.filterwarnings('ignore')
plt.style.use('seaborn-whitegrid')
data_dir = Path('/kaggle/input/santa-2022')

In [9]:
#By Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

df_image = pd.read_csv(data_dir / 'image.csv')
df_image

FileNotFoundError: [Errno 2] No such file or directory: '/kaggle/input/santa-2022/image.csv'

In [ ]:
#By Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

def df_to_image(df):
    side = int(len(df) ** 0.5) 
    return df.set_index(['x', 'y']).to_numpy().reshape(side, side, -1)

#Santas Drawings

In [ ]:
#By Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

image = df_to_image(df_image)

In [ ]:
#By Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

radius = 128
fig,ax = plt.subplots(3,3)
ax=ax.flatten()
fig.set_figheight(15)
fig.set_figwidth(15)
for i in range(9): 
    if i ==0:
        ax[i].matshow(image, extent=(-radius, radius+1, -radius, radius+1))
        ax[i].grid(None)
    if i > 0:
        kmeans_df = copy.deepcopy(df_image)
        kmeans_df['plot_x'] = kmeans_df['x']+128
        kmeans_df['plot_y'] = kmeans_df['y']+128
        kmeans_df['plot_x'] = kmeans_df['plot_x']/256
        kmeans_df['plot_y'] = kmeans_df['plot_y']/256
        km = KMeans(n_clusters=i,random_state = 0)
        km.fit(kmeans_df[['r','g','b']])
        kmeans_df['label'] = km.labels_
        ax[i].scatter(kmeans_df['plot_x'],kmeans_df['plot_y'],marker="o",c=kmeans_df['label'])
        ax[i].set_title("kmeans:{}".format(i))
        ax[i].grid(None)
plt.show()

In [ ]:
#By Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

kmeans_df = copy.deepcopy(df_image)
kmeans_df['plot_x'] = kmeans_df['x']+128
kmeans_df['plot_y'] = kmeans_df['y']+128
kmeans_df['plot_x'] = kmeans_df['plot_x']/256
kmeans_df['plot_y'] = kmeans_df['plot_y']/256
km = KMeans(n_clusters=2,random_state = 0)
km.fit(kmeans_df[['r','g','b']])
kmeans_df['label'] = km.labels_
kmeans_2 = df_to_image(kmeans_df[['x','y','label']])
radius = 128
fig, ax = plt.subplots(figsize=(10, 10))
ax.matshow(kmeans_2, extent=(-radius, radius+1, -radius, radius+1))
ax.add_patch(plt.Rectangle((-radius, radius+1), 86, -105, color="white", fill=False, linewidth=3))
# 
ax.add_patch(plt.Rectangle((50, radius+1), 78, -105, color="white", fill=False, linewidth=3))
ax.grid(None);

#What about C-Number Draw? Isn't it lovely? So Cute.

In [ ]:
#By C-Number https://www.kaggle.com/code/cnumber/lower-bound-using-minimum-spanning-tree
def hash_to_xy(i):
    return i//N, i%N
def xy_to_hash(x,y):
    return x*N+y
def get_cost(i, j):
    ix, iy = hash_to_xy(i)
    jx, jy = hash_to_xy(j)
    d = np.abs(ix-jx)+np.abs(iy-jy)
    return np.sum(np.abs(image[ix,iy]-image[jx,jy]))*3 + np.sqrt(d)
N = 257
NN = N*N
radius = 128
mat = dok_matrix((NN, NN), dtype=np.float64)
mst = minimum_spanning_tree(mat)
for i in tqdm.trange(NN):
    x, y = hash_to_xy(i)
    for dx in range(-8, 9):
        for dy in range(-8, 9):
            nx, ny = x+dx, y+dy
            if np.abs(dx)+np.abs(dy) > 8:
                continue
            if nx<0 or N<=nx or ny<0 or N<=ny:
                continue
            j = xy_to_hash(nx, ny)
            cost = get_cost(i, j)
            mat[i,j] = cost
mst = minimum_spanning_tree(mat)
edges = list(zip(*mst.nonzero()))
lines = []
for i, j in edges:
    ix, iy = hash_to_xy(i)
    jx, jy = hash_to_xy(j)
    d = np.sqrt(np.abs(ix-jx)**2 + np.abs(iy-jy)**2)
    # if d >= 1.8:
    lines.append([[iy - radius, radius - ix],[jy - radius, radius - jx]])
lc = mc.LineCollection(lines, colors='b')

fig = plt.figure(figsize=(20,20))
ax = fig.add_subplot(111)
ax.add_collection(lc)
ax.matshow(image, extent=(-radius-0.5, radius+0.5, -radius-0.5, radius+0.5))
ax.grid(None)

ax.autoscale()
fig.show()

In [ ]:
#By Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

# Then find out how many colors in each line are the same (similar)
baseline_poi = 125
color_baseline = df_image[df_image['x']==baseline_poi].sort_values('y')[['y','r','g','b']].reset_index(drop = True)
color_baseline.columns = ['y','r_baseline','g_baseline','b_baseline']

split_df = copy.deepcopy(df_image)
split_df = pd.merge(split_df,color_baseline,on = 'y')

def get_split(per):
    rgb_list = ['label_{}_per{}'.format(element,per)for element in ['r','g','b']]
    for color_now in ['r','g','b']:
        label_name = 'label_{}_per{}'.format(color_now,per)
        baseline_name = '{}_baseline'.format(color_now)
        left_bound = split_df[color_now] >= split_df[baseline_name]*(1-per/100)
        right_bound = split_df[color_now] <= split_df[baseline_name]*(1+per/100)
        split_df[label_name] = left_bound&right_bound
        split_df[label_name] = split_df[label_name].apply(int)
    rgb_name = 'label_rgb_per{}'.format(per)
    split_df[rgb_name] = split_df[rgb_list].sum(axis = 1)
    split_df[rgb_name] = split_df[rgb_name].apply(lambda element:1 if element == 3 else 0)
    return(split_df)
for i in range(20):
    split_df = get_split(i)

In [ ]:
#By Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

radius = 128
fig,ax = plt.subplots(2,4)
ax=ax.flatten()
fig.set_figheight(10)
fig.set_figwidth(20)
cols = ['label_r_per0','label_g_per0','label_b_per0','label_rgb_per0',
        'label_r_per1','label_g_per1','label_b_per1','label_rgb_per1']
for i in range(len(cols)): 
    ax[i].set_title(cols[i])
    ax[i].matshow(df_to_image(split_df[['x','y',cols[i]]]), extent=(-radius, radius+1, -radius, radius+1))
    ax[i].grid(None)

#Try to join the next Santas Competition.

And deliver something like those guys did. 

In [ ]:
#By Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

fig,ax = plt.subplots(1,2)
ax=ax.flatten()
fig.set_figheight(8)
fig.set_figwidth(20)
ax[0].matshow(df_to_image(split_df[['x','y','label_rgb_per4']]), extent=(-radius, radius+1, -radius, radius+1))
ax[0].grid(None)
ax[0].set_title("background mask")
ax[1].matshow(image, extent=(-radius, radius+1, -radius, radius+1))
ax[1].grid(None)
ax[1].set_title("original image")
plt.show()

#Be inspired by those professionals and join that Kaggle Competitions.

#Acknowledgements:

Victor Dumetz https://www.kaggle.com/code/victordumetz/gaslfr-svg-visualisation

Griffh https://www.kaggle.com/code/griffh/santa-eda-about-color/notebook

C-Number https://www.kaggle.com/code/cnumber/lower-bound-using-minimum-spanning-tree

![](https://i.pinimg.com/474x/b7/5c/73/b75c73e335cc1e79deb683191451c6c1.jpg)https://br.pinterest.com/pin/me--140806223847194/